In [3]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [4]:
# DELETE BEFORE PUBLISHING
# This is just here so you can preview the styling on your local machine

from IPython.core.display import HTML
HTML("""
<style>

.usecase-title, .usecase-duration, .usecase-section-header {
    padding-left: 15px;
    padding-bottom: 10px;
    padding-top: 10px;
    padding-right: 15px;
    background-color: #0f9295;
    color: #fff;
}

.usecase-title {
    font-size: 1.7em;
    font-weight: bold;
}

.usecase-authors, .usecase-level, .usecase-skill {
    padding-left: 15px;
    padding-bottom: 7px;
    padding-top: 7px;
    background-color: #baeaeb;
    font-size: 1.4em;
    color: #121212;
}

.usecase-level-skill  {
    display: flex;
}

.usecase-level, .usecase-skill {
    width: 50%;
}

.usecase-duration, .usecase-skill {
    text-align: right;
    padding-right: 15px;
    padding-bottom: 8px;
    font-size: 1.4em;
}

.usecase-section-header {
    font-weight: bold;
    font-size: 1.2em;
}

.usecase-subsection-header, .usecase-subsection-blurb {
    font-weight: bold;
    font-size: 1.2em;
    color: #121212;
}

.usecase-subsection-blurb {
    font-size: 1em;
    font-style: italic;
}
</style>
""")

<div class="usecase-title">Entertainment Location Projections</div>

<div class="usecase-authors"><b>Authored by: </b>Barkha Javed, Jack Pham</div>

<div class="usecase-duration"><b>Duration:</b> 75 mins</div>

<div class="usecase-level-skill">
    <div class="usecase-level"><b>Level: </b>Intermediate</div>
    <div class="usecase-skill"><b>Pre-requisite Skills: </b>Python</div>
</div>

 <div class="usecase-section-header">Scenario</div>

**As a City of Melbourne council worker, I want to visualise and provide statistics on upcoming activities and planned works in entertainment and leisure, so that I can understand impact for my local area.**

I also want to know which entertainment locations are projected as growth areas. 

<div class="usecase-section-header">What this Use Case will teach you</div>

At the end of this use case you will understand what entertainment and leisure venues are in a small area, and if the locations is projected as a growth area.

This means learning how to:

* Load and examine data on seating capacity of cafes, restaurants and pubs
* Load and examine data on cafe, bistro, restaurant seats
* Load and examine data for city activities and planned works
* Load and examine pedestrian traffic to see current volumes for entertainment locations
* Visualise information from the datasets
* Review growth projections about entertainment locations



<div class="usecase-section-header">A brief introduction to the datasets used</div>

#### Census of Land Use and Employment (CLUE) 
The City of Melbourne conducts a census of all local businesses every two years. The last published survey was in 2020, the next survey results are expected soon.

The CLUE datasets contain information on venues:
* CLUE Blocks spatial layer
* Bar, tavern, pub patron capacity
* Cafe, restaurant, bistro seats 

#### City Activities and Planned Works
* Geospatial events data, includes types such as traffic management, sport and recreation, reserved parking, public and  private events

#### Other datasets of interest
* Hourly pedestrian counts from sensors located across the city 
* Public and school holidays dataset

<div class="usecase-section-header">Setup</div>

In [5]:
#Libraries to be installed
##!pip -q is to give less output
!pip -q install sodapy
!pip -q install seaborn
!pip -q install pandas
!pip -q install matplotlib
!pip -q install numpy
!pip -q install nbconvert
!pip -q install keyboard
!pip -q install geopandas
!pip -q install requests
!pip -q install folium
!pip -q install statsmodels

     |████████████████████████████████| 62 kB 1.5 MB/s 
     |████████████████████████████████| 58 kB 3.6 MB/s 
     |████████████████████████████████| 1.1 MB 8.0 MB/s 
     |████████████████████████████████| 7.8 MB 49.4 MB/s 
     |████████████████████████████████| 16.6 MB 54.9 MB/s 


In [6]:
#load libraries
import os
import io
import time
import keyboard
import warnings
warnings.filterwarnings('ignore')
from datetime import datetime
import requests
import zipfile


import numpy as np
import pandas as pd
from sodapy import Socrata

from urllib.request import urlopen
import json

import folium
from folium import Choropleth, Circle, Marker
from folium.plugins import HeatMap, MarkerCluster

from IPython.core.display import display, HTML
import geopandas as gpd

from pandas.io.json import json_normalize
import plotly.express as px
import seaborn as sns
import matplotlib.pyplot as plt
%matplotlib inline
from matplotlib import style
style.use('ggplot')

#Socrata client connection
client = Socrata('data.melbourne.vic.gov.au', '9UAGAvkem9fqXDhBLElapjazL', None)


In [7]:
#set default values
this_decade = (pd.Timestamp.today().year)-10
this_year = pd.Timestamp.today().year
y3 = (pd.Timestamp.today().year)-3
y2 = (pd.Timestamp.today().year)-2
y1 = (pd.Timestamp.today().year)-1

<div class="usecase-section-header">Load and Transform Data</div>

## Load CLUE blocks

Load the CLUE blocks geographical boundary layer to to display CLUE information.

In [9]:
# spatial layer used to map CLUE datasets to CLUE blocks
ds_url = "/content/drive/MyDrive/Colab Notebooks/blocks-for-census-of-land-use-and-employment-clue.geojson"
clueblocks = gpd.read_file(ds_url)



## Load Bar, tavern, pub patron capacity

In [10]:
#Load Bar, tavern, pub patron capacity dataset
ds_url = "https://data.melbourne.vic.gov.au/explore/dataset/bars-and-pubs-with-patron-capacity/download/?format=geojson&timezone=Australia/Sydney&lang=en"
data_json = requests.get(ds_url).json()
df = pd.DataFrame.from_dict(data_json)
print(df.shape)

#this flattens the features
df_btp_capacity=json_normalize(df['features'])

#rename columns
df_btp_capacity.rename(columns={"properties.longitude": "lon", "properties.latitude": "lat"
                        ,"properties.census_year":"census_year"
                        ,"properties.location ":"location"
                        ,"properties.building_address":"building_address"
                        , "properties.trading_name":"trading_name"
                        ,"properties.property_id":"property_id"
                        , "properties.business_address":"business_address"
                        ,"properties.clue_small_area":"clue_small_area"
                        ,"properties.block_id":"block_id"
                        ,"properties.number_of_patrons":"number_of_patrons"
                        ,"properties.base_property_id":"base_property_id"}
               ,inplace = True)


(4402, 2)


In [11]:
#transform
integer_columns = ['census_year', 'block_id', 'property_id', 'base_property_id', 'number_of_patrons']
str_columns = ['building_address','business_address', 'clue_small_area', 'trading_name']
df_btp_capacity[integer_columns] = df_btp_capacity[integer_columns].astype(int)
df_btp_capacity[str_columns] = df_btp_capacity[str_columns].astype(str)


In [12]:
#limit data to past decade
df_btp_capacity=df_btp_capacity.query("census_year >= @this_decade")


## Load Cafe, restaurant, bistro seats 

In [13]:
#Load Cafe, restaurant, bistro seats dataset
ds_url = "https://data.melbourne.vic.gov.au/explore/dataset/cafes-and-restaurants-with-seating-capacity/download/?format=geojson&timezone=Australia/Sydney&lang=en"
data_json = requests.get(ds_url).json()
df = pd.DataFrame.from_dict(data_json)

#this flattens the features
df_crb = json_normalize(df['features'])

In [14]:
#rename
df_crb.rename(columns={"properties.longitude": "lon", "properties.latitude": "lat"
                        ,"properties.seating_type":"seating_type"
                        ,"properties.census_year":"census_year"
                        ,"properties.location":"location"
                        ,"properties.building_address":"building_address"
                        ,"properties.trading_name":"trading_name"
                        ,"properties.property_id":"property_id"
                        ,"properties.base_property_id":"base_property_id"
                        ,"properties.business_address":"business_address"
                        ,"properties.clue_small_area":"clue_small_area"
                        ,"properties.block_id":"block_id"
                       , "properties.industry_anzsic4_description":"industry_anzsic4_description"
                        ,"properties.number_of_seats":"number_of_seats"
                        ,"properties.industry_anzsic4_code":"industry_anzsic4_code"}
               ,inplace = True)


In [15]:
#transform
integer_columns = ['census_year', 'block_id', 'property_id', 'base_property_id', 'number_of_seats']
str_columns = ['clue_small_area', 'trading_name','industry_anzsic4_description','seating_type']
df_crb[integer_columns] = df_crb[integer_columns].astype(int)
df_crb[str_columns] = df_crb[str_columns].astype(str)

#drop NaN values
df_crb.dropna(subset=['business_address'])


#latest decade
df_crb = df_crb.query("census_year >= 2012") 

print(df_crb.shape)
df_crb.head(5).T

#limit data to past decade
df_crb=df_crb.query("census_year >= @this_decade")


(33651, 19)


### Merge CLUE venue seats, capacity and activities datasets

In [16]:
#Merge CLUE block data
clue_venues = df_crb.append(df_btp_capacity)

#combine seats or patrons values as capacity
clue_venues['capacity'] = clue_venues[['number_of_seats', 'number_of_patrons']].bfill(axis=1).iloc[:, 0]

#fill remaining nulls
clue_venues.fillna(0, inplace=True)  

## Load City Activities and Planned Works 

Load spatial layer

In [17]:
capw_file ="city-activities-and-planned-works.geojson"
capw=gpd.read_file(capw_file)

ERROR:fiona._env:city-activities-and-planned-works.geojson: No such file or directory


DriverError: ignored

In [18]:
# spatial layer used to map city activity planned works
ds_url = "https://data.melbourne.vic.gov.au/explore/dataset/city-activities-and-planned-works/download/?format=geojson&timezone=Australia/Sydney&lang=en"
data_json = requests.get(ds_url).json()
df = pd.DataFrame.from_dict(data_json)

#this flattens the features
df_capw = json_normalize(df['features'])

In [19]:
df_capw.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 605 entries, 0 to 604
Data columns (total 14 columns):
 #   Column                     Non-Null Count  Dtype 
---  ------                     --------------  ----- 
 0   type                       605 non-null    object
 1   geometry.coordinates       605 non-null    object
 2   geometry.type              605 non-null    object
 3   properties.location        603 non-null    object
 4   properties.status          605 non-null    object
 5   properties.notes           500 non-null    object
 6   properties.end_date        605 non-null    object
 7   properties.geo_point_2d    605 non-null    object
 8   properties.activity_id     605 non-null    object
 9   properties.classification  605 non-null    object
 10  properties.geometry        605 non-null    object
 11  properties.start_date      605 non-null    object
 12  properties.source_id       605 non-null    object
 13  properties.small_area      605 non-null    object
dtypes: object(

In [20]:
#rename columns
df_capw.rename(columns={"properties.start_date": "start_date", "properties.location": "location"
                        ,"properties.activity_id":"activity_id", "properties.end_date":"end_date"
                        ,"properties.status":"status", "properties.source_id":"source_id"
                        ,"properties.notes":"notes", "properties.classification":"classification"
                        ,"properties.small_area":"small_area"}
               ,inplace = True)


#look at events that are still current
df_capw = df_capw[(df_capw.classification.isin(['Event','PublicEvent','Sport/Recreation']))]

df_capw.dropna(subset=['properties.geometry'])

#Convert to date, add columns
df_capw['start_dt'] = pd.to_datetime(df_capw.start_date).dt.date
df_capw['start_year'] = pd.to_datetime(df_capw.start_dt).dt.year
df_capw['start_month'] = pd.to_datetime(df_capw.start_dt).dt.month

#drop columns
df_capw = df_capw.drop(['geometry.type', 'type'], axis=1)

#filter found there are records with value 2921-11-19 00:00:00, exclude these
df_capw = df_capw.loc[(df_capw['end_date'] < '2065-01-01')]
df_capw['end_dt'] = pd.to_datetime(df_capw.end_date).dt.date
df_capw['end_year'] = pd.to_datetime(df_capw.end_dt).dt.year
df_capw['end_month'] = pd.to_datetime(df_capw.end_dt).dt.month



In [21]:
#Range of years
df_capw.start_year.unique()

array([2018, 2022, 2020, 2023, 2019, 2021])

In [22]:
#Merge CLUE block data
clue_venues_capw=clue_venues.append(df_capw)

#combine seats or patrons values as capacity
clue_venues_capw['year'] = clue_venues_capw[['census_year', 'start_year']].bfill(axis=1).iloc[:, 0]
clue_venues_capw['year'] = clue_venues_capw['year'].astype(int)
clue_venues_capw['small_area_tag'] = clue_venues_capw[['clue_small_area', 'small_area']].bfill(axis=1).iloc[:, 0]
clue_venues_capw['description_tag'] = clue_venues_capw[['industry_anzsic4_description', 'classification']].bfill(axis=1).iloc[:, 0]
#clue_venues_capw['geometry'] = clue_venues_capw[['geometry.coordinates','x_coordinate' +','+'y_coordinate']].bfill(axis=1).iloc[:, 0]

#fill remaining nulls
clue_venues_capw.fillna(0, inplace=True)  

In [23]:
clue_venues_capw.small_area_tag.unique()

array(['Melbourne (CBD)', 'West Melbourne (Residential)', 'Docklands',
       'Carlton', 'Parkville', 'North Melbourne',
       'West Melbourne (Industrial)', 'Kensington', 'East Melbourne',
       'Melbourne (Remainder)', 'Southbank', 'Port Melbourne',
       'South Yarra'], dtype=object)

In [24]:
#create data frames per year for some visuals
#the latest data is for the past year
clue_venues_y3=clue_venues_capw.query("year == @y3")
clue_venues_y2=clue_venues_capw.query("year == @y2")
clue_venues_y1=clue_venues_capw.query("year >= @y1")


## Other datasets of interest

The sensor locations data will be used to see traffic in vicinity of an entertainment location. The venue capacity data uses small area for the block. We will try to assign sensor location to a block.

The pedestrian traffic will show us what areas people are visiting and during what part of the day. This can be used to evaluate if the entertainment venue capacity is low, sufficient, or high. 


### Load pedestrian sensor locations

In [25]:
#Pedestrian sensor location data
ds_url = "https://data.melbourne.vic.gov.au/explore/dataset/pedestrian-counting-system-sensor-locations/download/?format=geojson&timezone=Australia/Sydney&lang=en"
data_json = requests.get(ds_url).json()
df = pd.DataFrame.from_dict(data_json)

#this flattens the features
sensor_data = json_normalize(df['features'])



In [26]:
sensor_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 117 entries, 0 to 116
Data columns (total 14 columns):
 #   Column                         Non-Null Count  Dtype  
---  ------                         --------------  -----  
 0   type                           117 non-null    object 
 1   geometry.type                  117 non-null    object 
 2   geometry.coordinates           117 non-null    object 
 3   properties.sensor_name         117 non-null    object 
 4   properties.direction_1         86 non-null     object 
 5   properties.sensor_description  117 non-null    object 
 6   properties.direction_2         86 non-null     object 
 7   properties.latitude            117 non-null    float64
 8   properties.location            117 non-null    object 
 9   properties.sensor_id           117 non-null    int64  
 10  properties.installation_date   117 non-null    object 
 11  properties.longitude           117 non-null    float64
 12  properties.status              117 non-null    obj

In [27]:
#rename columns
sensor_data.rename(columns={"properties.sensor_name": "sensor_name","properties.direction_1":"direction_1"
                        ,"properties.sensor_description":"sensor_description"
                        ,"properties.direction_2":"direction_2"
                        ,"properties.latitude":"latitude"
                        ,"properties.location": "location","properties.sensor_id":"sensor_id"
                        ,"properties.installation_date":"installation_date"
                        ,"properties.longitude":"longitude"
                        ,"properties.status":"status"
                        ,"properties.note":"note"
                        }
               ,inplace = True)


In [28]:
sensor_data[['lat', 'lon']] = sensor_data[['latitude', 'longitude']].astype(float)
sensor_data.head(5).T

0  \
type                                                 Feature   
geometry.type                                          Point   
geometry.coordinates            [144.95678789, -37.81295822]   
sensor_name                                        261Will_T   
direction_1                                            South   
sensor_description    William St - Little Lonsdale St (West)   
direction_2                                            North   
latitude                                          -37.812958   
location                        [-37.81295822, 144.95678789]   
sensor_id                                                108   
installation_date                                 2022-10-08   
longitude                                         144.956788   
status                                                     A   
note                                                     NaN   
lat                                               -37.812958   
lon                                               144.956788   

                                                                  1  \
type                                                        Feature   
geometry.type                                                 Point   
geometry.coordinates                   [144.96291897, -37.82011242]   
sensor_name                                                SanBri_T   
direction_1                                                   South   
sensor_description                                 Sandridge Bridge   
direction_2                                                   North   
latitude                                                 -37.820112   
location                               [-37.82011242, 144.96291897]   
sensor_id                                                        14   
installation_date                                        2009-03-24   
longitude                                                144.962919   
status                                                            R   
note                  Sensor relocated to sensor ID 25 on 2/10/2019   
lat                                                      -37.820112   
lon                                                      144.962919   

                                                 2  \
type                                       Feature   
geometry.type                                Point   
geometry.coordinates  [144.96291897, -37.82011242]   
sensor_name                               SanBri_T   
direction_1                                  South   
sensor_description                Sandridge Bridge   
direction_2                                  North   
latitude                                -37.820112   
location              [-37.82011242, 144.96291897]   
sensor_id                                       14   
installation_date                       2019-09-25   
longitude                               144.962919   
status                                           A   
note                                           NaN   
lat                                     -37.820112   
lon                                     144.962919   

                                                 3  \
type                                       Feature   
geometry.type                                Point   
geometry.coordinates  [144.96115421, -37.82556207]   
sensor_name                                BoCoL_T   
direction_1                                    NaN   
sensor_description     Boyd Community Hub- Library   
direction_2                                    NaN   
latitude                                -37.825562   
location              [-37.82556207, 144.96115421]   
sensor_id                                       90   
installation_date                       2015-08-11   
longitude                               144.961154   
status                                           A   
note                                           NaN   
lat                              

### Load pedestrian traffic hourly counts data

In [31]:
#URL / API method will need to be updated
#Pedestrian foot count data 
ds_url = "https://data.melbourne.vic.gov.au/api/datasets/1.0/pedestrian-counting-system-monthly-counts-per-hour/attachments/pedestrian_counting_system_monthly_counts_per_hour_may_2009_to_14_dec_2022_csv_zip/"
filename = '/content/drive/MyDrive/Colab Notebooks/Pedestrian_Counting_System_Monthly_counts_per_hour_may_2009_to_14_dec_2022.csv'

r = requests.get(ds_url)
z = zipfile.ZipFile(io.BytesIO(r.content))
z.extractall()

sensor_traffic = pd.read_csv(filename, sep=',')

In [32]:
#rename columns
sensor_traffic.rename(columns={"Date_Time": "date_time","Year":"year"
                        ,"Month":"month"
                        ,"Mdate":"mdate"
                        ,"Day":"day"
                        ,"Time": "time"
                        ,"Sensor_ID":"sensor_id"
                        ,"Sensor_Name":"sensor_name"
                        ,"Hourly_Counts":"hourly_counts"
                        }
               ,inplace = True)

In [33]:
sensor_traffic.head(5).T

0                              1  \
ID                                   2887628                        2887629   
date_time      November 01, 2019 05:00:00 PM  November 01, 2019 05:00:00 PM   
year                                    2019                           2019   
month                               November                       November   
mdate                                      1                              1   
day                                   Friday                         Friday   
time                                      17                             17   
sensor_id                                 34                             39   
sensor_name             Flinders St-Spark La                   Alfred Place   
hourly_counts                            300                            604   

                                           2                              3  \
ID                                   2887630                        2887631   
date_time      November 01, 2019 05:00:00 PM  November 01, 2019 05:00:00 PM   
year                                    2019                           2019   
month                               November                       November   
mdate                                      1                              1   
day                                   Friday                         Friday   
time                                      17                             17   
sensor_id                                 37                             40   
sensor_name                  Lygon St (East)   Lonsdale St-Spring St (West)   
hourly_counts                            216                            627   

                                           4  
ID                                   2887632  
date_time      November 01, 2019 05:00:00 PM  
year                                    2019  
month                               November  
mdate                                      1  
day                                   Friday  
time                                      17  
sensor_id                                 36  
sensor_name                  Queen St (West)  
hourly_counts                            774

In [34]:
#Add date column
sensor_traffic['date'] = pd.to_datetime(sensor_traffic.date_time).dt.date
sensor_traffic['month_num'] = pd.to_datetime(sensor_traffic.date_time).dt.month

#Add day of week column
sensor_traffic['dow'] = pd.to_datetime(sensor_traffic.date_time).dt.day_of_week

#convert fields to integer
sensor_traffic['mdate']=sensor_traffic['mdate'].astype(int)
sensor_traffic['time']=sensor_traffic['time'].astype(int)
sensor_traffic['year']=sensor_traffic['year'].astype(int)
sensor_traffic['mdate']=sensor_traffic['mdate'].astype(int)
sensor_traffic['hourly_counts']=sensor_traffic['hourly_counts'].astype(int)
sensor_traffic['sensor_id']=sensor_traffic['sensor_id'].astype(int)

# Mesh pedestrian sensor location and foot traffic datasets
sensor_traffic = pd.merge(sensor_traffic, sensor_data, on='sensor_id', how='inner')

#filter to this decade
sensor_traffic=sensor_traffic.query("year >= @this_decade")

#Add column for day (5am to 5pm) or night (6pm to 4am) traffic
sensor_traffic['day_counts']   = np.where(((sensor_traffic['time']>4) & (sensor_traffic['time']<18)),
                                          sensor_traffic['hourly_counts'] , 0).astype(int)
sensor_traffic['night_counts'] = np.where(sensor_traffic['day_counts']==0,sensor_traffic['hourly_counts']
                                          , 0).astype(int)

In [44]:
sensor_traffic.rename(columns={"sensor_name_x": "sensor_name"}
               ,inplace = True)
sensor_traffic.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4527683 entries, 0 to 4977922
Data columns (total 30 columns):
 #   Column                Dtype  
---  ------                -----  
 0   ID                    int64  
 1   date_time             object 
 2   year                  int64  
 3   month                 object 
 4   mdate                 int64  
 5   day                   object 
 6   time                  int64  
 7   sensor_id             int64  
 8   sensor_name           object 
 9   hourly_counts         int64  
 10  date                  object 
 11  month_num             int64  
 12  dow                   int64  
 13  type                  object 
 14  geometry.type         object 
 15  geometry.coordinates  object 
 16  sensor_name_y         object 
 17  direction_1           object 
 18  sensor_description    object 
 19  direction_2           object 
 20  latitude              float64
 21  location              object 
 22  installation_date     object 
 23  longitu

In [45]:
sensor_traffic.year.unique()

array([2019, 2014, 2015, 2016, 2017, 2018, 2020, 2021, 2022, 2013, 2012])

In [57]:
#group by traffic for past decade 2012 to 2022
#average day_counts, night_counts, hourly counts per month, year,all areas

this_year = (pd.Timestamp.today().year) 
sensor_ds=sensor_traffic.query("year >= @this_year")

#will use this to show traffic in entertainment locations this year
sensor_ds_yearll = sensor_traffic.groupby(['year','sensor_name','lat','lon'],as_index=False).agg(
    {'hourly_counts': 'mean','day_counts':'mean','night_counts':'mean'})

sensor_ds_year = sensor_traffic.groupby(['year'],as_index=False).agg(
    {'hourly_counts': 'mean','day_counts':'mean','night_counts':'mean'})

sensor_ds_ym = sensor_ds.groupby(['year','month_num'],as_index=False).agg(
    {'hourly_counts': 'mean','day_counts':'mean','night_counts':'mean'})

sensor_ds_ymd = sensor_ds.groupby(['year','month_num', 'dow'],as_index=False).agg(
    {'hourly_counts': 'mean','day_counts':'mean','night_counts':'mean'})

In [58]:
sensor_ds_yearll.head(5)

year                 sensor_name        lat         lon  hourly_counts  \
0  2012        Australia on Collins -37.815734  144.965210     711.437158   
1  2012              Birrarung Marr -37.818629  144.971694     345.953893   
2  2012  Bourke Street Mall (North) -37.813494  144.965153    1059.452983   
3  2012  Bourke Street Mall (South) -37.813807  144.965167    1146.758652   
4  2012       Collins Place (North) -37.813449  144.973054     341.213115   

   day_counts  night_counts  
0  615.525159     95.911999  
1  229.489071    116.464822  
2  850.250569    209.202413  
3  962.091985    184.666667  
4  289.785291     51.427823

<div class="usecase-section-header">Data Analysis</div>

## Entertainment location venue seating and patron capacity

Map the number of seats or number of patrons from the combined clue venue data of bars, pubs and taverns and cafes, bistros and restaurants.

In [35]:
# Display the choropleth map
fig = px.choropleth_mapbox(
        
    clue_venues_capw, #dataset
    geojson=clueblocks, #CLUE Block spatial data
        
    locations='block_id', 
    color='capacity', 
    color_continuous_scale='sunset', #colour scale
    range_color=(0, df_btp_capacity['number_of_patrons'].max()), #range for the colour scale
        
    featureidkey="block_id",
    mapbox_style="stamen-terrain", #map style
    zoom=13.25, #zoom level
    
    center = {"lat": -37.81216592937499, "lon": 144.961812290625}, # set the map centre coordinates on Melbourne
    opacity=0.7,
        
    hover_name='small_area_tag', #title of the pop up box
    hover_data={'year':True,'block_id':True,'number_of_patrons':True,
                'number_of_seats':True, 'capacity' : True,
                'lon':False,'lat':False}, #values to display in the popup box   
    labels={'number_of_patrons':'Number of Patrons','block_id':'Block Id',
            'number_of_seats':'Number of Seats',
            'capacity':'Capacity','census_year':'Census Year'
           },
    title='Venue Capacity', #Title for plot
    width=950, height=800 #dimensions of plot in pixels

 )

#show year 3
fig1 = px.scatter_mapbox(
    
    clue_venues_y3, lat="lat", lon="lon",
    opacity=0.8,
    hover_name='small_area_tag', # the title of the hover pop up box
    hover_data={'year':True,'block_id':True,'number_of_patrons':True,
                'number_of_seats':True, 'capacity' : True,
                'lat':False,'lon':False}, #values to display in the popup box
    color_discrete_sequence=['purple'],   
    labels={'capacity':'Capacity','block_id':'Block Id',
            'census_year':'Census Year'}, # defines labels for
    
)

#show year 2
fig2 = px.scatter_mapbox(
    
    clue_venues_y2, lat="lat", lon="lon",
    opacity=0.7,
    hover_name='small_area_tag', # the title of the hover pop up box
    hover_data={'year':True,'block_id':True,'number_of_patrons':True,
                'number_of_seats':True, 'capacity' : True,
                'lat':False,'lon':False}, #values to display in the popup box
    color_discrete_sequence=['plum'],   
    labels={'capacity':'Capacity','block_id':'Block Id',
            'census_year':'Census Year'}, # defines labels for
    
)

#show year 1
fig3 = px.scatter_mapbox(
    
    clue_venues_y1, lat="lat", lon="lon",
    opacity=0.75,
    hover_name='clue_small_area', #title of the pop up box
    hover_data={'year':True,'block_id':True,'number_of_patrons':True,
                'number_of_seats':True, 'capacity' : True, 'description_tag': True,
                'lat':False,'lon':False}, #values to display in the popup box
    color_discrete_sequence=['cyan'],   
    size_max=20, zoom=10,
    labels={'capacity':'Capacity','block_id':'Block Id','description_tag':'Description',
            'census_year':'Census Year'}, #labels
    
)


# labels={'source_id':'Source_Id', 'classification':'Classification',
#           'start_year':'Start Year',
#          'end_year':'End Year'}, 


#differentiate recent years for interest
fig.add_trace(fig3.data[0])
fig.add_trace(fig2.data[0])
fig.add_trace(fig1.data[0])
fig.update_geos(fitbounds="locations", visible=True)

fig.show()


## What areas have the most capacity?

Assess venue capacity to accommodate both number of seats and number of patrons. 

In [36]:
#group by clue small area this year
clue_venues_ty_by_area = clue_venues_y1.groupby(
    ['small_area_tag']).agg('sum')
clue_venues_ty_by_area.sort_values(by=['capacity'], ascending=False).reset_index()[['small_area_tag','capacity']]

small_area_tag  capacity
0                Melbourne (CBD)  142755.0
1                      Southbank   31249.0
2                      Docklands   26513.0
3                        Carlton   17946.0
4                 East Melbourne    9981.0
5          Melbourne (Remainder)    9339.0
6                North Melbourne    6266.0
7                     Kensington    6165.0
8                      Parkville    4506.0
9   West Melbourne (Residential)    3373.0
10                Port Melbourne     987.0
11                   South Yarra     927.0
12   West Melbourne (Industrial)      68.0

In [37]:
#group by clue small area this year
clue_venues_ty_by_area = clue_venues_y1.groupby(
    ['industry_anzsic4_description']).agg('sum')
clue_venues_ty_by_area.sort_values(
    by=['number_of_seats'], ascending=False).reset_index()[['industry_anzsic4_description','number_of_seats']]

industry_anzsic4_description  number_of_seats
0                               Cafes and Restaurants         132243.0
1                              Pubs, Taverns and Bars          16461.0
2                                   Catering Services           5806.0
3                                       Accommodation           5661.0
4                              Takeaway Food Services           5514.0
5   Horse and Dog Racing Administration and Track ...           3660.0
6                                 Clubs (Hospitality)           1598.0
7   Sports and Physical Recreation Venues, Grounds...           1326.0
8                  Non-Residential Property Operators           1108.0
9                                    Casino Operation            805.0
10                                 Religious Services            600.0
11   Bakery Product Manufacturing (Non-factory based)            270.0
12                   Other Specialised Food Retailing            210.0
13               Other Interest Group Services n.e.c.            202.0
14                                   Museum Operation            200.0
15         Zoological and Botanical Gardens Operation            198.0
16                    Performing Arts Venue Operation            196.0
17  Amusement and Other Recreational Activities n....            125.0
18                          Other Gambling Activities            100.0
19                          Performing Arts Operation             83.0
20                       Newspaper and Book Retailing             79.0
21  Health and Fitness Centres and Gymnasia Operation             72.0
22         Automotive Body, Paint and Interior Repair             36.0
23               Other Administrative Services n.e.c.             31.0
24                          Motion Picture Exhibition             30.0
25                                      Car Retailing             24.0
26                                   Flower Retailing             21.0
27                 Other Store-Based Retailing n.e.c.             20.0
28                      Fruit and Vegetable Retailing             18.0
29                     Supermarket and Grocery Stores             18.0
30            Other Food Product Manufacturing n.e.c.             16.0
31                Telecommunication Goods Wholesaling             16.0
32                                                  0              0.0

### View City Planned Activities & Pedestrian Traffic



In [59]:
# The map shows the 'geometry' polygons, to identify which sensor locations are impacted 
# by the planned activity and event 

outline1 = {'fillColor': 'indigo', 'color': 'purple'}

#Create a map object centered on Melbourne
map = folium.Map(location=[-37.81216592937499, 
                           144.961812290625], 
                          zoom_start=14)

#Add the current events to the map
#folium.GeoJson(data=capw, style_function=lambda x:outline1, 
#               name='Planned Activity and Works',).add_to(map)

#folium.GeoJson(data=current_act.adjacent, style_function=lambda x:style2).add_to(map)
#folium.GeoJson(data=current_act.near, style_function=lambda x:style3).add_to(map)


#Add all sensor locations
location_data = sensor_ds_yearll
for i in range(0,len(location_data)): 
    folium.Marker(
       icon=folium.Icon(color="pink", icon="info-sign"),
       location=[location_data.iloc[i]['lat'], location_data.iloc[i]['lon']],
       popup=location_data.iloc[i]['sensor_name'],
       name='Traffic Y1'
   ).add_to(map)


folium.LayerControl().add_to(map)
map

<div class="usecase-section-header">Statistics</div>

Charts

Jack:
Top locations by seats outdoors and indoors
Top locations by number of patrons
Top entertainment locations with activities in 2022

Barkha:
What is the pedestrian traffic for these locations, also day and night
Are the venues busier in the evenings
Are any venues busier in the day

Bonus:
Can we make a selection to see breakdown for a location dropdown list?

Or focus on the red areas for venues example Docklands

In [41]:
clue_venues_y1

type geometry.type  \
24626  Feature         Point   
24627  Feature         Point   
24628  Feature         Point   
24629  Feature         Point   
24630  Feature         Point   
...        ...           ...   
390          0             0   
571          0             0   
600          0             0   
603          0             0   
604          0             0   

                                    geometry.coordinates  \
24626                             [144.95651, -37.82098]   
24627                             [144.95651, -37.82098]   
24628                             [144.96578, -37.81868]   
24629                             [144.96865, -37.81868]   
24630                             [144.96994, -37.81778]   
...                                                  ...   
390    [[[144.9603815625, -37.8138854546], [144.96001...   
571    [[[144.9585470939, -37.8134912382], [144.95859...   
600    [[[144.9698941704, -37.8059129062], [144.96986...   
603    [[[144.9579106613, -37.8145937539], [144.95753...   
604    [[[144.9462924035, -37.7863128672], [144.94628...   

                                                location     seating_type  \
24626                             [-37.82098, 144.95651]   Seats - Indoor   
24627                             [-37.82098, 144.95651]  Seats - Outdoor   
24628                             [-37.81868, 144.96578]  Seats - Outdoor   
24629                             [-37.81868, 144.96865]  Seats - Outdoor   
24630                             [-37.81778, 144.96994]  Seats - Outdoor   
...                                                  ...              ...   
390    Queen Street: QS - Between Bourke St & Lonsdal...                0   
571    Lonsdale Street: LS - Between Queen St & Willi...                0   
600             Carlton Gardens: CG - Lawn 10/Dalai Lama                0   
603    William Street: WS - Between Bourke St & Lonsd...                0   
604                              Royal Park: RP - Lawn 7                0   

       census_year  property_id  base_property_id           trading_name  \
24626       2021.0     611394.0          611394.0              Food Hall   
24627       2021.0     611394.0          611394.0       Nandos Northbank   
24628       2021.0     104034.0          104034.0  Arbory Bar and Eatery   
24629       2021.0     110655.0          110655.0          Riverland Bar   
24630       2021.0     578319.0          573333.0            ACMI Events   
...            ...          ...               ...                    ...   
390            0.0          0.0               0.0                      0   
571            0.0          0.0               0.0                      0   
600            0.0          0.0               0.0                      0   
603            0.0          0.0               0.0                      0   
604            0.0          0.0               0.0                      0   

       block_id  ...       small_area    start_dt start_year start_month  \
24626       1.0  ...                0           0        0.0         0.0   
24627       1.0  ...                0           0        0.0         0.0   
24628       4.0  ...                0           0        0.0         0.0   
24629       6.0  ...                0           0        0.0         0.0   
24630       6.0  ...                0           0        0.0         0.0   
...         ...  ...              ...         ...        ...         ...   
390         0.0  ...  Melbourne (CBD)  2022-02-01     2022.0         2.0   
571         0.0  ...  Melbourne (CBD)  2022-03-01     2022.0         3.0   
600         0.0  ...          Carlton  2023-05-01     2023.0         5.0   
603         0.0  ...  Melbourne (CBD)  2022-02-01     2022.0         2.0   
604         0.0  ...        Parkville  2021-12-22     2021.0        12.0   

           end_dt  end_year  end_month  year   small_area_tag  \
24626           0       0.0        0.0  2021  Melbourne (CBD)   
24627           0      

In [42]:
clue_venues_s1 =clue_venues_y1.groupby(['small_area_tag','description_tag'], as_index=False).agg(
    {'capacity': 'sum'})
clue_venues_s1



small_area_tag  \
0                        Carlton   
1                        Carlton   
2                        Carlton   
3                        Carlton   
4                        Carlton   
..                           ...   
94  West Melbourne (Residential)   
95  West Melbourne (Residential)   
96  West Melbourne (Residential)   
97  West Melbourne (Residential)   
98  West Melbourne (Residential)   

                                      description_tag  capacity  
0                                                   0    2769.0  
1                                       Accommodation     465.0  
2                               Cafes and Restaurants   13268.0  
3                                               Event       0.0  
4                           Motion Picture Exhibition      30.0  
..                                                ...       ...  
94         Automotive Body, Paint and Interior Repair      36.0  
95                              Cafes and Restaurants    1548.0  
96                             Pubs, Taverns and Bars    1040.0  
97  Sports and Physical Recreation Venues, Grounds...     134.0  
98                             Takeaway Food Services      73.0  

[99 rows x 3 columns]

<div class="usecase-section-header">Projections</div>

In [50]:
df =  sensor_ds_year
fig = px.scatter(df,  x="year", y=["hourly_counts","day_counts","night_counts"],  trendline="ols")
fig.show()

Add narrative

In [51]:
#Model for forecasting location growth using datasets loaded earlier

#Todo:
#Initial linear regression, compare to another model LSTM

#Techniques for controlling jittering
#Normalise data to 28 day period per month example 28/31 * measure
# eg:  28/31 * pedestrian count


#look at areas with high demand based on pedestrian traffic by month, dow and hod




<div class="usecase-section-header">Summary</div>

<div class="usecase-section-header">References</div>

City of Melbourne Open Data Team, 2014 - 2021,'Bar, tavern, pub patron capacity 2020', City of Melbourne, date retrieved 26 Nov 2022, <https://data.melbourne.vic.gov.au/Business/Bar-tavern-pub-patron-capacity-2020/9hjf-8i2d>

City of Melbourne Open Data Team, 2014 - 2021,'Cafe, restaurant, bistro seats 2020', City of Melbourne, date retrieved 26 Nov 2022, <https://data.melbourne.vic.gov.au/Business/Cafe-restaurant-bistro-seats-2020/dyqx-cfn5>

City of Melbourne Open Data Team, 2014 - 2021,'City Activities and Planned Works', City of Melbourne, date retrieved 26 Nov 2022, <https://data.melbourne.vic.gov.au/Events/City-Activities-and-Planned-Works/txcy-uafv>

City of Melbourne Open Data Team, 2014 - 2021,'Pedestrian Counting System - Monthly (counts per hour)', City of Melbourne, date retrieved 03 Dec 2022, <https://dev.socrata.com/foundry/data.melbourne.vic.gov.au/b2ak-trbp>

City of Melbourne Open Data Team, 2014 - 2021,'Pedestrian Counting System - Sensor Locations', City of Melbourne, date retrieved 03 Dec 2022, <https://data.melbourne.vic.gov.au/Transport/Pedestrian-Counting-System-Sensor-Locations/h57g-5234>

O'Brien J, et al., 2020, 'Covid 19 in Australia', covid19data.com.au, date retrieved 03 Dec 2022, <https://www.covid19data.com.au/>

Victorian Government, 'Victorian Government - Important Dates API', Victorian Government date retrieved 12 Dec 2022, <https://www.developer.vic.gov.au/index.php?option=com_apiportal&view=apitester&usage=api&apiName=Victorian%20Government%20-%20Important%20Dates%20API&sn=Victorian%20Government%20-%20Important%20Dates%20API&Itemid=153&tab=tests&apiId=65c5cce0-efcb-4dba-bdde-f391d3a35dc2&menuId=153&apiVersion=2.0.0&managerId=1&renderTool=1&type=rest>

In [ ]:
#save notebook, required so that step to convert to html, writes latest results to file
#adapt for other OS, this is for Windows
keyboard.press_and_release('ctrl+s')

!jupyter nbconvert  usecase_entertainment_location_projections.ipynb --to html --log-level WARN